In [207]:
import warnings
warnings.filterwarnings('ignore')
import pandas as pd
import math
#from sklearn.cross_validation import KFold
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.wordnet import WordNetLemmatizer
lemma=WordNetLemmatizer()
stop=set(stopwords.words('english'))
import seaborn as sns

In [208]:
import pandas as pd
datafile_train=r'Consumer_Complaints_train.csv'
datafile_test=r'Consumer_Complaints_test_share.csv'
cd_train=pd.read_csv(datafile_train)
cd_test=pd.read_csv(datafile_test)

In [209]:
cd_train.head(8)

Date received                  Product                  Sub-product  \
0    2014-05-15              Credit card                          NaN   
1    2014-09-18  Bank account or service  (CD) Certificate of deposit   
2    2014-03-13         Credit reporting                          NaN   
3    2015-07-17              Credit card                          NaN   
4    2014-11-20              Credit card                          NaN   
5    2014-06-26                 Mortgage               Other mortgage   
6    2012-09-28                 Mortgage               Other mortgage   
7    2015-05-06                 Mortgage                 FHA mortgage   

                                      Issue       Sub-issue  \
0                         Billing statement             NaN   
1  Making/receiving payments, sending money             NaN   
2    Incorrect information on credit report  Account status   
3                         Billing statement             NaN   
4                         Transaction issue             NaN   
5  Loan modification,collection,foreclosure             NaN   
6  Loan servicing, payments, escrow account             NaN   
7  Loan modification,collection,foreclosure             NaN   

                        Consumer complaint narrative  \
0                                                NaN   
1                                                NaN   
2                                                NaN   
3  My credit card statement from US Bank, XXXX. X...   
4                                                NaN   
5                                                NaN   
6                                                NaN   
7  I have a mortgage with Quicken Loans. From XXX...   

                            Company public response                Company  \
0                                               NaN  Wells Fargo & Company   
1                                               NaN      Santander Bank US   
2                                               NaN                Equifax   
3  Company chooses not to provide a public response           U.S. Bancorp   
4                                               NaN        Bank of America   
5                                               NaN        Bank of America   
6                                               NaN                  Ocwen   
7                                               NaN          Quicken Loans   

  State ZIP code            Tags Consumer consent provided? Submitted via  \
0    MI    48342  Older American                        NaN           Web   
1    PA    18042             NaN                        NaN      Referral   
2    CA    92427             NaN                        NaN      Referral   
3    GA    305XX  Older American           Consent provided           Web   
4    MA    02127             NaN                        NaN           Web   
5    WI    54313             NaN                        NaN      Referral   
6    FL    33168             NaN                        NaN      Referral   
7    GA    300XX             NaN           Consent provided           Web   

  Date sent to company     Company response to consumer Timely response?  \
0           2014-05-16          Closed with explanation              Yes   
1           2014-09-24                           Closed              Yes   
2           2014-04-03  Closed with non-monetary relief              Yes   
3           2015-07-17      Closed with monetary relief              Yes   
4           2014-11-28          Closed with explanation              Yes   
5           2014-07-01          Closed with explanation              Yes   
6           2012-10-01          Closed with explanation              Yes   
7           2015-05-06          Closed with explanation              Yes   

  Consumer disputed?  Complaint ID  
0                 No        856103  
1                 No       1034666  
2                 No        756363  
3                 No       1474177  
4   

In [210]:
cd_train['Consumer disputed?']=np.where(cd_train['Consumer disputed?']=="Yes",0,1)

In [211]:
cd_train.head(3)

Date received                  Product                  Sub-product  \
0    2014-05-15              Credit card                          NaN   
1    2014-09-18  Bank account or service  (CD) Certificate of deposit   
2    2014-03-13         Credit reporting                          NaN   

                                      Issue       Sub-issue  \
0                         Billing statement             NaN   
1  Making/receiving payments, sending money             NaN   
2    Incorrect information on credit report  Account status   

  Consumer complaint narrative Company public response                Company  \
0                          NaN                     NaN  Wells Fargo & Company   
1                          NaN                     NaN      Santander Bank US   
2                          NaN                     NaN                Equifax   

  State ZIP code            Tags Consumer consent provided? Submitted via  \
0    MI    48342  Older American                        NaN           Web   
1    PA    18042             NaN                        NaN      Referral   
2    CA    92427             NaN                        NaN      Referral   

  Date sent to company     Company response to consumer Timely response?  \
0           2014-05-16          Closed with explanation              Yes   
1           2014-09-24                           Closed              Yes   
2           2014-04-03  Closed with non-monetary relief              Yes   

   Consumer disputed?  Complaint ID  
0                   1        856103  
1                   1       1034666  
2                   1        756363

In [212]:
for col in ['Date received','Date sent to company']:
    cd_train[col]=pd.to_datetime(cd_train[col],infer_datetime_format=True)
    cd_test[col]=pd.to_datetime(cd_test[col],infer_datetime_format=True)

In [213]:
cd_train['day_diff']=pd.to_numeric((cd_train['Date sent to company']-cd_train['Date received'])/np.timedelta64(1, 'M'))
cd_test['day_diff']=pd.to_numeric((cd_test['Date sent to company']-cd_test['Date received'])/np.timedelta64(1, 'M'))

In [214]:
for col in ['Date received','Date sent to company']:
    cd_train.drop([col],1,inplace=True)
    cd_test.drop([col],1,inplace=True)

In [215]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company public response : 10
Company : 3276
State : 62
ZIP code : 25962
Tags : 3
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [216]:
for col in cd_test.select_dtypes(['object']).columns:
    print(col,':',cd_test[col].nunique())

Product : 12
Sub-product : 47
Issue : 94
Sub-issue : 67
Consumer complaint narrative : 18438
Company public response : 10
Company : 2237
State : 62
ZIP code : 17784
Tags : 3
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [217]:
cd_train['Tags'].value_counts()

Older American                   39064
Servicemember                    22592
Older American, Servicemember     5550
Name: Tags, dtype: int64

In [218]:
for col in cd_train['Tags']:
    print(col)

Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
Servicemember
Older American
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American, 

nan
nan
nan
nan
Servicemember
Older American
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
Ol

nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
Servicemember
Older American
Older American
nan
nan
Older American
nan
nan
Servicemember
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
Older American
Servicemember
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan

nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Servicemember
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
Ol

nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Servicemember
nan
nan
Servicemember
nan
Older American
nan
nan
nan
nan
nan
Older American
Older American, Servicemember
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
n

...

nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
Servicemember
nan
nan
Older American
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan

nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
Older American
Older American
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American, Servicemember
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan

nan
Older American
nan
Servicemember
nan
Older American
nan
nan
Servicemember
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
Servicemember
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American, Servicemember
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
Servicemember
Older American
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan


nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Older American
nan
Older American
nan
nan
Older American
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
Servicemember
Older American
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan

nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
Older American
Older American, Servicemember
Older American
Servicemember
nan
nan
nan
nan
nan
Older American
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Servicemember
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American, Servicemember
Older American
nan
nan
nan
Older American
nan
Older American, Servicemember
nan
nan
nan
Older American
nan
nan
nan
nan
nan
Older American
nan
nan
nan
Older American
nan
Older American
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
nan
nan
nan
nan
nan
nan
Servicemember
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
Older American
nan
nan
Older American, Servicemember
Older American, Servic

In [219]:
cd_train.isnull().sum()

Product                              0
Sub-product                     138473
Issue                                0
Sub-issue                       292625
Consumer complaint narrative    403327
Company public response         388029
Company                              0
State                             3839
ZIP code                          3848
Tags                            411215
Consumer consent provided?      342934
Submitted via                        0
Company response to consumer         0
Timely response?                     0
Consumer disputed?                   0
Complaint ID                         0
day_diff                             0
dtype: int64

In [123]:
for col in ['Tags','Company public response']:
    varname=col.replace('-','_').replace('?','').replace(" ",'_')+'_isNan'
    cd_train[varname]=np.where(pd.isnull(cd_train[col]),1,0)
    cd_train.drop([col],1,inplace=True)
    cd_test[varname]=np.where(pd.isnull(cd_test[col]),1,0)
    cd_test.drop([col],1,inplace=True)
    

In [124]:
cd_train.dtypes

Product                           object
Sub-product                       object
Issue                             object
Sub-issue                         object
Consumer complaint narrative      object
Company                           object
State                             object
ZIP code                          object
Consumer consent provided?        object
Submitted via                     object
Company response to consumer      object
Timely response?                  object
Consumer disputed?                 int32
Complaint ID                       int64
day_diff                         float64
Tags_isNan                         int32
Company_public_response_isNan      int32
dtype: object

In [125]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Product : 12
Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
State : 62
ZIP code : 25962
Consumer consent provided? : 4
Submitted via : 6
Company response to consumer : 7
Timely response? : 2


In [126]:
k=cd_train['State'].value_counts()
for val in k.axes[0][0:15]:
    varname='State_'+val.replace(',','_').replace(' ','_')
    cd_train[varname]=np.where(cd_train['State']==val,1,0)
    cd_test[varname]=np.where(cd_test['State']==val,1,0)
del cd_train['State']
del cd_test['State']

In [127]:
for col in ['Product','Submitted via','Company response to consumer','Timely response?']:
    
    temp=pd.get_dummies(cd_train[col],prefix=col,drop_first=True)
    cd_train=pd.concat([temp,cd_train],1)
    cd_train.drop([col],1,inplace=True)
    
    temp=pd.get_dummies(cd_test[col],prefix=col,drop_first=True)
    cd_test=pd.concat([temp,cd_test],1)
    cd_test.drop([col],1,inplace=True)


In [128]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Company : 3276
ZIP code : 25962
Consumer consent provided? : 4


In [129]:
cd_train.shape

(478421, 50)

In [130]:
cd_test.shape

(119606, 49)

In [131]:
for col in ['ZIP code','Company']:
    cd_train.drop([col],1,inplace=True)
    cd_test.drop([col],1,inplace=True)

In [132]:
for col in cd_train.select_dtypes(['object']).columns:
    print(col,':',cd_train[col].nunique())

Sub-product : 47
Issue : 95
Sub-issue : 68
Consumer complaint narrative : 74019
Consumer consent provided? : 4


In [133]:
for col in cd_test.select_dtypes(['object']).columns:
    print(col,':',cd_test[col].nunique())

Sub-product : 47
Issue : 94
Sub-issue : 67
Consumer complaint narrative : 18438
Consumer consent provided? : 4


In [134]:
cd_train['Super']=cd_train['Consumer consent provided?']+cd_train['Sub-product']+cd_train['Issue']+','+cd_train['Sub-issue']+','+cd_train['Consumer complaint narrative']
del cd_train['Issue']
del cd_train['Sub-issue']
del cd_train['Consumer complaint narrative']
del cd_train['Consumer consent provided?']
cd_train["Super"]=np.where(pd.isnull(cd_train["Super"]),'NaN',cd_train['Super'])
cd_train['Super'].astype(str)
    

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
478416    NaN
478417    NaN
478418    NaN
478419    NaN
478420    NaN
Name: Super, Length: 478421, dtype: object

In [135]:
cd_test['Super']=cd_test['Consumer consent provided?']+cd_test['Sub-product']+cd_test['Issue']+','+cd_test['Sub-issue']+','+cd_test['Consumer complaint narrative']
del cd_test['Issue']
del cd_test['Sub-issue']
del cd_test['Consumer consent provided?']
del cd_test['Consumer complaint narrative']
cd_test["Super"]=np.where(pd.isnull(cd_test["Super"]),'NaN',cd_test['Super'])
cd_test['Super'].astype(str)
    

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
119601    NaN
119602    NaN
119603    NaN
119604    NaN
119605    NaN
Name: Super, Length: 119606, dtype: object

In [136]:
cd_test.isnull().sum()

Timely response?_Yes                                                0
Company response to consumer_Closed with explanation                0
Company response to consumer_Closed with monetary relief            0
Company response to consumer_Closed with non-monetary relief        0
Company response to consumer_Closed with relief                     0
Company response to consumer_Closed without relief                  0
Company response to consumer_Untimely response                      0
Submitted via_Fax                                                   0
Submitted via_Phone                                                 0
Submitted via_Postal mail                                           0
Submitted via_Referral                                              0
Submitted via_Web                                                   0
Product_Consumer Loan                                               0
Product_Credit card                                                 0
Product_Credit repor

In [137]:
cd_train.isnull().sum()

Timely response?_Yes                                                 0
Company response to consumer_Closed with explanation                 0
Company response to consumer_Closed with monetary relief             0
Company response to consumer_Closed with non-monetary relief         0
Company response to consumer_Closed with relief                      0
Company response to consumer_Closed without relief                   0
Company response to consumer_Untimely response                       0
Submitted via_Fax                                                    0
Submitted via_Phone                                                  0
Submitted via_Postal mail                                            0
Submitted via_Referral                                               0
Submitted via_Web                                                    0
Product_Consumer Loan                                                0
Product_Credit card                                                  0
Produc

In [138]:
cd_train.head(4)

Timely response?_Yes  Company response to consumer_Closed with explanation  \
0                     1                                                  1      
1                     1                                                  0      
2                     1                                                  0      
3                     1                                                  0      

   Company response to consumer_Closed with monetary relief  \
0                                                  0          
1                                                  0          
2                                                  0          
3                                                  1          

   Company response to consumer_Closed with non-monetary relief  \
0                                                  0              
1                                                  0              
2                                                  1              
3                                                  0              

   Company response to consumer_Closed with relief  \
0                                                0   
1                                                0   
2                                                0   
3                                                0   

   Company response to consumer_Closed without relief  \
0                                                  0    
1                                                  0    
2                                                  0    
3                                                  0    

   Company response to consumer_Untimely response  Submitted via_Fax  \
0                                               0                  0   
1                                               0                  0   
2                                               0                  0   
3                                               0                  0   

   Submitted via_Phone  Submitted via_Postal mail  ...  State_PA  State_IL  \
0                    0                          0  ...         0         0   
1                    0                          0  ...         1         0   
2                    0                          0  ...         0         0   
3                    0                          0  ...         0         0   

   State_VA  State_MD  State_OH  State_NC  State_MI  State_AZ  State_WA  Super  
0         0         0         0         0         1         0         0    NaN  
1         0         0         0         0         0         0         0    NaN  
2         0         0         0         0         0         0         0    NaN  
3         0         0         0         0         0         0         0    NaN  

[4 rows x 45 columns]

In [139]:
cd_train['Super']

0         NaN
1         NaN
2         NaN
3         NaN
4         NaN
         ... 
478416    NaN
478417    NaN
478418    NaN
478419    NaN
478420    NaN
Name: Super, Length: 478421, dtype: object

In [38]:
###cd1_train,cd1_test=train_test_split(cd_train,test_size=0.2,random_state=2)

In [140]:
from sklearn.naive_bayes import MultinomialNB

In [141]:
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.wordnet import WordNetLemmatizer
lemma=WordNetLemmatizer()
stop=set(stopwords.words('english'))

In [142]:
def split_into_lemmas(message):
    words=word_tokenize(message)
    words_sans_stop=[]
    for word in words:
        if word in stop:continue
        words_sans_stop.append(word)
    return[lemma.lemmatize(word) for word in words_sans_stop]

In [143]:
tfidf=TfidfVectorizer(analyzer=split_into_lemmas,min_df=10,max_df=3000)

In [144]:
tfidf.fit(cd_train['Super'])

TfidfVectorizer(analyzer=<function split_into_lemmas at 0x000000A4B7FA1D38>,
                binary=False, decode_error='strict',
                dtype=<class 'numpy.float64'>, encoding='utf-8',
                input='content', lowercase=True, max_df=3000, max_features=None,
                min_df=10, ngram_range=(1, 1), norm='l2', preprocessor=None,
                smooth_idf=True, stop_words=None, strip_accents=None,
                sublinear_tf=False, token_pattern='(?u)\\b\\w\\w+\\b',
                tokenizer=None, use_idf=True, vocabulary=None)

In [45]:
train_data=tfidf.transform(cd_train['Super'])

In [145]:
train_data

<478421x6925 sparse matrix of type '<class 'numpy.float64'>'
	with 1006402 stored elements in Compressed Sparse Row format>

In [146]:
test_data=tfidf.transform(cd_test['Super'])

In [147]:
clf=MultinomialNB()

In [148]:
clf.fit(train_data,cd_train['Consumer disputed?'])

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [149]:
Final_data=tfidf.transform(cd_train['Super'])

In [150]:
p=clf.predict_proba(Final_data)

In [151]:
p.shape

(478421, 2)

In [152]:
p[:,0]

array([0.21201201, 0.21201201, 0.21201201, ..., 0.21201201, 0.21201201,
       0.21201201])

In [153]:
clf.classes_

array([0, 1])

In [154]:
cd_train['Tfidf']=np.where(p[:,0]>=0.5,0,1)

In [155]:
del cd_train['Super']

In [156]:
del cd_train['Sub-product']

In [157]:
Test_Final_data=tfidf.transform(cd_test['Super'])

In [158]:
Test_Final_data

<119606x6925 sparse matrix of type '<class 'numpy.float64'>'
	with 244927 stored elements in Compressed Sparse Row format>

In [159]:
r=clf.predict_proba(Test_Final_data)

In [160]:
r

array([[0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       ...,
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799],
       [0.21201201, 0.78798799]])

In [161]:
cd_test['Tfidf']=np.where(r[:,0]>=0.5,1,0)

In [162]:
cd_train.dtypes

Timely response?_Yes                                              uint8
Company response to consumer_Closed with explanation              uint8
Company response to consumer_Closed with monetary relief          uint8
Company response to consumer_Closed with non-monetary relief      uint8
Company response to consumer_Closed with relief                   uint8
Company response to consumer_Closed without relief                uint8
Company response to consumer_Untimely response                    uint8
Submitted via_Fax                                                 uint8
Submitted via_Phone                                               uint8
Submitted via_Postal mail                                         uint8
Submitted via_Referral                                            uint8
Submitted via_Web                                                 uint8
Product_Consumer Loan                                             uint8
Product_Credit card                                             

In [163]:
cd_test.dtypes

Timely response?_Yes                                              uint8
Company response to consumer_Closed with explanation              uint8
Company response to consumer_Closed with monetary relief          uint8
Company response to consumer_Closed with non-monetary relief      uint8
Company response to consumer_Closed with relief                   uint8
Company response to consumer_Closed without relief                uint8
Company response to consumer_Untimely response                    uint8
Submitted via_Fax                                                 uint8
Submitted via_Phone                                               uint8
Submitted via_Postal mail                                         uint8
Submitted via_Referral                                            uint8
Submitted via_Web                                                 uint8
Product_Consumer Loan                                             uint8
Product_Credit card                                             

In [164]:
cd1_train,cd1_test=train_test_split(cd_train,test_size=0.2,random_state=2)

In [165]:
del cd_test['Super']

In [166]:
del cd_test['Sub-product']

In [179]:
cd_test.shape

(119606, 43)

In [189]:
x=cd1_train.drop(['Consumer disputed?','Complaint ID'],1)
y=cd1_train['Consumer disputed?']
#k=cd1_test.drop(['Consumer disputed?','Complaint ID'],1)
#m=cd1_test['Consumer disputed?']


In [193]:
y.shape

(382736,)

In [184]:
m.value_counts()

1    75566
0    20119
Name: Consumer disputed?, dtype: int64

In [185]:
y.shape

(382736,)

In [186]:
m.shape

(95685,)

In [190]:
from sklearn.linear_model import LogisticRegression

In [191]:
clf=LogisticRegression()

In [192]:
clf.fit(x,y)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='warn', tol=0.0001, verbose=0,
                   warm_start=False)

In [196]:
prediction=clf.predict(x)

In [197]:
from sklearn.metrics import roc_auc_score

In [198]:
prediction

array([1, 1, 1, ..., 1, 1, 1])

In [199]:
m.shape

(95685,)

In [200]:
roc_auc_score(prediction,x)

ValueError: bad input shape (382736, 42)

In [201]:
cd_test.head(5)

Timely response?_Yes  Company response to consumer_Closed with explanation  \
0                     1                                                  1      
1                     1                                                  1      
2                     1                                                  0      
3                     1                                                  0      
4                     1                                                  1      

   Company response to consumer_Closed with monetary relief  \
0                                                  0          
1                                                  0          
2                                                  0          
3                                                  0          
4                                                  0          

   Company response to consumer_Closed with non-monetary relief  \
0                                                  0              
1                                                  0              
2                                                  0              
3                                                  1              
4                                                  0              

   Company response to consumer_Closed with relief  \
0                                                0   
1                                                0   
2                                                0   
3                                                0   
4                                                0   

   Company response to consumer_Closed without relief  \
0                                                  0    
1                                                  0    
2                                                  1    
3                                                  0    
4                                                  0    

   Company response to consumer_Untimely response  Submitted via_Fax  \
0                                               0                  0   
1                                               0                  0   
2                                               0                  0   
3                                               0                  0   
4                                               0                  0   

   Submitted via_Phone  Submitted via_Postal mail  ...  State_PA  State_IL  \
0                    0                          0  ...         0         0   
1                    0                          0  ...         0         0   
2                    0                          0  ...         0         0   
3                    0                          1  ...         0         0   
4                    0                          0  ...         0         0   

   State_VA  State_MD  State_OH  State_NC  State_MI  State_AZ  State_WA  Tfidf  
0         0         0         0         0         0         0         0      0  
1         0         0         0         0         0         0         0      0  
2         0         0         0         0         0         0         0      0  
3         0         0         0         0         0         0         0      0  
4         0         0         0         0         0         0         0      0  

[5 rows x 43 columns]

In [202]:
cd_test['Complaint ID']

0          675956
1         1858795
2           32637
3         1731374
4          501487
           ...   
119601     153482
119602    2023523
119603    1413678
119604     732458
119605    1235226
Name: Complaint ID, Length: 119606, dtype: int64

In [203]:
Final_prediction=np.where(clf.predict(cd_test.drop(['Complaint ID'],1))==1,"No","Yes")

In [204]:
Final_prediction

array(['Yes', 'Yes', 'Yes', ..., 'Yes', 'Yes', 'Yes'], dtype='<U3')

In [205]:
submission=pd.DataFrame(list(zip(cd_test['Complaint ID'],list(prediction))),
                       columns=['Complaint ID','Consumer disputed?'])

In [76]:
m.value_counts()

1    75566
0    20119
Name: Consumer disputed?, dtype: int64

In [77]:
submission['Consumer disputed?'].value_counts()

1    95586
0       99
Name: Consumer disputed?, dtype: int64

In [206]:
submission.to_csv('Nishant_Joshi_P1_Part2.csv',index=False)

In [98]:
cd_train['Consumer disputed?'].value_counts()

1    376990
0    101431
Name: Consumer disputed?, dtype: int64